# Imports and Data

In [12]:
# Third-party

import xarray as xr

import torch
import torch.nn as nn
from torch.utils.data import DataLoader

import lightning as L
from lightning.pytorch.callbacks import ModelCheckpoint, EarlyStopping
from lightning.pytorch import Trainer

# Local imports

from weather_data_class_v3 import WeatherData

ds = xr.open_dataset('data_850/2022_850_SA_coarsen.nc')
ds.load()


<xarray.Dataset> Size: 197MB
Dimensions:    (time: 8760, latitude: 16, longitude: 32)
Coordinates:
  * time       (time) datetime64[ns] 70kB 2022-01-01 ... 2022-12-31T23:00:00
  * longitude  (longitude) float32 128B 16.31 16.81 17.31 ... 30.81 31.31 31.81
  * latitude   (latitude) float32 64B -34.89 -34.39 -33.89 ... -27.89 -27.39
Data variables:
    q          (time, latitude, longitude) float64 36MB 0.007599 ... 0.009553
    t          (time, latitude, longitude) float64 36MB 282.4 282.5 ... 284.3
    u          (time, latitude, longitude) float64 36MB 14.09 13.71 ... 3.188
    v          (time, latitude, longitude) float64 36MB -0.8432 -1.022 ... 4.144
    w          (time, latitude, longitude) float64 36MB -0.002005 ... 0.1457
    wspd       (time, latitude, longitude) float32 18MB 14.12 13.75 ... 5.228
Attributes:
    Conventions:  CF-1.6
    history:      2024-05-28 12:36:03 GMT by grib_to_netcdf-2.28.1: /opt/ecmw...
    wspd_units:   m/s

# Model Setup

In [33]:
class SimpleMLP(L.LightningModule):
    def __init__(self, 
                 input_size, 
                 forcing_size, 
                 output_size, 
                 lr = 0.0001, 
                 steps = 1, 
                 lat = 16, 
                 lon = 32,
                 weigths = False,
                 intervals = 1):
        
        super(SimpleMLP, self).__init__()

        self.save_hyperparameters()

        self.fc1 = nn.Linear(input_size + forcing_size, 128)  
        self.fc2 = nn.Linear(128, 64) 
        self.fc3 = nn.Linear(64, output_size) 

        self.loss_fn = nn.MSELoss()

        self.steps = steps

        self.lat = lat
        self.lon = lon

        self.lr = lr

        self.intervals = intervals
        
        if weigths:
            self.apply(self.init_weights)

    def init_weights(self, m):
        if isinstance(m, nn.Linear):
            nn.init.xavier_uniform_(m.weight)  
            if m.bias is not None:
                nn.init.constant_(m.bias, 0) 

    def forward(self, X, F):

        batch_size = X.size(0)
        X = X.reshape(batch_size, -1)  

        inputs = torch.cat((X, F), dim=1)  

        x = torch.relu(self.fc1(inputs)) 
        x = torch.relu(self.fc2(x))
        x = self.fc3(x)  

        return x.reshape(-1, 1, self.lat, self.lon)
    
    def training_step(self, batch, batch_idx):
        x, F, y = batch  

        loss = self.auto_rollout(x, F, y)

        self.log("train_loss", loss, on_step=True, on_epoch=True) 
        return loss

    def validation_step(self, batch, batch_idx):
        x, F, y = batch  
 
        loss = self.auto_rollout(x, F, y)

        self.log("val_loss", loss, on_step=False, on_epoch=True) 
        
        return loss
    
    def auto_rollout(self, x, F, y):

        cumulative_loss = 0.0
        current_input = x.clone()
        current_F = F.clone()

        for step in range(self.steps): 
            # print('Step: ', step)
            
            y_hat = self(current_input, current_F)

            loss = self.loss_fn(y_hat, y[:, step].reshape(-1, 1, self.lat, self.lon))
            cumulative_loss += loss  
            
            current_input = torch.cat((current_input[:, 1:], y_hat), dim=1)

            hour = current_F[:, 0]
            month = current_F[:, 1]
            
            hour = (hour + self.intervals) % 24

            current_F = torch.stack((hour, month), dim=1).float()

        return cumulative_loss
    
    def configure_optimizers(self):
        optimizer = torch.optim.AdamW(self.parameters(), lr= self.lr)

        scheduler = torch.optim.lr_scheduler.ReduceLROnPlateau(optimizer, mode='min', patience=5, verbose=True)
        
        return {"optimizer": optimizer, "lr_scheduler": {"scheduler": scheduler, "monitor": "val_loss"}}
    

from UNetPyTorch import *

class build_res_unet_time_(nn.Module):
    def __init__(self, in_c, out_c, start_size = 64):
        super().__init__()

        ''' Encoder 1 '''
        self.c11 = nn.Conv2d(in_c + 2, start_size, kernel_size=3, padding=1)  # in_c + 2 to account for time inputs
        self.br1 = batchnorm_relu(start_size)
        self.c12 = nn.Conv2d(start_size, start_size, kernel_size=3, padding=1)
        self.c13 = nn.Conv2d(in_c + 2, start_size, kernel_size=1, padding=0)  # Shortcut feature

        """ Encoder 2 and 3 """
        self.r2 = residual_block(start_size, start_size * 2, stride=2)
        self.r3 = residual_block(start_size * 2, start_size * 4, stride=2)

        """ Bridge """
        self.r4 = residual_block(start_size * 4, start_size * 8, stride=2)

        """ Decoder """
        self.d1 = decoder_block(start_size * 8, start_size * 4)
        self.d2 = decoder_block(start_size * 4, start_size * 2)
        self.d3 = decoder_block(start_size * 2, start_size)

        """ Output """
        self.output = nn.Conv2d(start_size, out_c, kernel_size=1, padding=0)
        # self.sigmoid = nn.Sigmoid()

    def forward(self, weather_data, time_input):
        # weather_data shape: (batch_size, window_size, lat, lon)
        # time_input shape: (batch_size, window_size, 2) where 2 corresponds to (hour of day, month of year)

        batch_size, window_size, lat, lon = weather_data.shape

        # Reshape weather_data to (batch_size, window_size, 1, lat, lon)
        weather_data = weather_data.view(batch_size, window_size, lat, lon)

        # Expand time_input to match the spatial dimensions of the weather data
        time_input = time_input.view(batch_size, 2)  # (batch_size, window_size, 2)

        # Expand to match spatial dimensions (lat, lon) and channel 2 for (hour, month)
        time_input_expanded = time_input.unsqueeze(-1).unsqueeze(-1)  # Add spatial dimensions
        time_input_expanded = time_input_expanded.expand(-1, -1, lat, lon)  # Now shape is (batch_size, 2, lat, lon)

        # Concatenate along the channel axis
        combined_input = torch.cat([weather_data, time_input_expanded], dim=1)  # New shape: (batch_size, in_c + 2, lat, lon)

        """ Encoder 1 """
        x = self.c11(combined_input)
        x = self.br1(x)
        x = self.c12(x)
        s = self.c13(combined_input)
        skip1 = x + s

        """ Encoder 2 and 3 """
        skip2 = self.r2(skip1)
        skip3 = self.r3(skip2)

        """ Bridge """
        b = self.r4(skip3)

        """ Decoder """
        d1 = self.d1(b, skip3)
        d2 = self.d2(d1, skip2)
        d3 = self.d3(d2, skip1)

        """ Output """
        output = self.output(d3)
        # output = self.sigmoid(output)

        return output


# Training

In [34]:
window_size = 5
steps = 13
batch_size = 32
intervals = 6

model_class = WeatherData(ds, window_size=window_size, steps=steps, use_forcings=True, intervals=intervals)
model_class.assign_model(build_res_unet_time_(model_class.window_size, 1))


Data split
Data normalized


In [35]:
model_class.plot_pred_target(seed=0, frame_rate=8, levels=10)

c:\Users\23603526\Documents\GitHub\1_WindSpeedForecasting\weather_data_class_v3.py:390: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  F = torch.tensor(F).float()


In [36]:
ar_steps = 1

model = SimpleMLP(
        model_class.input_size, 
        model_class.forcing_size, 
        model_class.output_size,
        steps=ar_steps,
        weigths=True,
        intervals=intervals
    )


train_loader = DataLoader(WeatherData(ds, 
                                    window_size=window_size, 
                                    steps=ar_steps, 
                                    intervals=intervals, 
                                    data_split='train'), 
                                    batch_size=batch_size, 
                                    shuffle=True,
                                    num_workers=4)

val_loader = DataLoader(WeatherData(ds,
                                    window_size=window_size,
                                    steps=ar_steps,
                                    intervals=intervals,
                                    data_split='val'), 
                                    batch_size=batch_size, 
                                    shuffle=False,
                                    num_workers=4)

checkpoint_callback = ModelCheckpoint(
    monitor="val_loss",      
    dirpath="checkpoints/",  
    filename=f"best_model_{ar_steps}_steps",
    save_top_k=1,            
    mode="min"              
)

early_stopping_callback = EarlyStopping(
    monitor="val_loss",      
    patience=5,             
    mode="min",              
    verbose=True
)

trainer = Trainer(
    max_epochs=10,
    callbacks=[checkpoint_callback, early_stopping_callback],
    check_val_every_n_epoch=1
)


Data split
Data normalized


GPU available: False, used: False
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs


Data split
Data normalized


In [37]:
trainer.fit(model, train_loader, val_loader)

c:\Users\23603526\AppData\Local\Programs\Python\Python311\Lib\site-packages\lightning\pytorch\callbacks\model_checkpoint.py:653: Checkpoint directory C:\Users\23603526\Documents\GitHub\1_WindSpeedForecasting\checkpoints exists and is not empty.
c:\Users\23603526\AppData\Local\Programs\Python\Python311\Lib\site-packages\torch\optim\lr_scheduler.py:28: UserWarning: The verbose parameter is deprecated. Please use get_last_lr() to access the learning rate.
  warnings.warn("The verbose parameter is deprecated. Please use get_last_lr() "

  | Name    | Type    | Params
------------------------------------
0 | fc1     | Linear  | 328 K 
1 | fc2     | Linear  | 8.3 K 
2 | fc3     | Linear  | 33.3 K
3 | loss_fn | MSELoss | 0     
------------------------------------
369 K     Trainable params
0         Non-trainable params
369 K     Total params
1.478     Total estimated model params size (MB)


Sanity Checking: |          | 0/? [00:00<?, ?it/s]

c:\Users\23603526\AppData\Local\Programs\Python\Python311\Lib\site-packages\lightning\pytorch\trainer\connectors\data_connector.py:441: The 'val_dataloader' does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` to `num_workers=11` in the `DataLoader` to improve performance.
c:\Users\23603526\AppData\Local\Programs\Python\Python311\Lib\site-packages\lightning\pytorch\trainer\connectors\data_connector.py:441: The 'train_dataloader' does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` to `num_workers=11` in the `DataLoader` to improve performance.


Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

...

Metric val_loss improved by 0.005 >= min_delta = 0.0. New best score: 0.464


Validation: |          | 0/? [00:00<?, ?it/s]

Metric val_loss improved by 0.000 >= min_delta = 0.0. New best score: 0.464


Validation: |          | 0/? [00:00<?, ?it/s]

`Trainer.fit` stopped: `max_epochs=10` reached.


In [10]:
model_class = WeatherData(ds, window_size=15, steps=13, use_forcings=True, intervals=3)

model = SimpleMLP(
        model_class.input_size, 
        model_class.forcing_size, 
        model_class.output_size,
    )

In [38]:
model_class.assign_model(model)
# model_class.load_model('models\MLP_15to1_s32_multi_3.pth')

model_class.plot_pred_target(seed=0, frame_rate=8, levels=10)

c:\Users\23603526\Documents\GitHub\1_WindSpeedForecasting\weather_data_class_v3.py:390: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  F = torch.tensor(F).float()


# Testing and development

In [43]:
import torch
from torch.utils.data import Dataset, DataLoader

class WindSpeedDataset(Dataset):
    def __init__(self, data, window_size=3, steps=2, interval=2):
        self.data = data
        self.window_size = window_size
        self.steps = steps
        self.interval = interval

    def __len__(self):
        # Calculate the number of batches
        return len(self.data) - (self.window_size + self.steps) * self.interval + self.interval

    def __getitem__(self, idx):
        # Calculate starting index for the window

        x = self.data[idx:idx + self.window_size * self.interval:self.interval]
        y = self.data[idx + self.window_size * self.interval:idx + self.window_size * self.interval + self.steps * self.interval:self.interval]
        return torch.tensor(x, dtype=torch.float32), torch.tensor(y, dtype=torch.float32)

# Example data
data = torch.arange(0, 25)

# Create dataset and dataloader
dataset = WindSpeedDataset(data, window_size=5, steps=5, interval=2)
dataloader = DataLoader(dataset, batch_size=1, shuffle=True)

# Display the batches
for batch_idx, (x, y) in enumerate(dataloader):
    print(f"Batch {batch_idx+1}: x as {x.numpy().flatten()} and y as {y.numpy().flatten()}")


Batch 1: x as [ 2.  4.  6.  8. 10.] and y as [12. 14. 16. 18. 20.]
Batch 2: x as [ 6.  8. 10. 12. 14.] and y as [16. 18. 20. 22. 24.]
Batch 3: x as [1. 3. 5. 7. 9.] and y as [11. 13. 15. 17. 19.]
Batch 4: x as [ 3.  5.  7.  9. 11.] and y as [13. 15. 17. 19. 21.]
Batch 5: x as [ 5.  7.  9. 11. 13.] and y as [15. 17. 19. 21. 23.]
Batch 6: x as [0. 2. 4. 6. 8.] and y as [10. 12. 14. 16. 18.]
Batch 7: x as [ 4.  6.  8. 10. 12.] and y as [14. 16. 18. 20. 22.]


C:\Users\23603526\AppData\Local\Temp\ipykernel_39236\1420455633.py:20: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  return torch.tensor(x, dtype=torch.float32), torch.tensor(y, dtype=torch.float32)
